Here, we will use manually defined functions, as well as the pyAudioAnalysis library to featurize mp3 samples of audio data.

In [1]:
# import required modules 
import pandas as pd
from pyAudioAnalysis import audioBasicIO
from pyAudioAnalysis import audioFeatureExtraction
import sys,json, os 
import numpy as np

def stats(matrix):
    mean=np.mean(matrix)
    std=np.std(matrix)
    maxv=np.amax(matrix)
    minv=np.amin(matrix)
    median=np.median(matrix)

    output=np.array([mean,std,maxv,minv,median])
    
    return output

def convert_mono(filename):
    mono=filename[0:-4]+'_mono.wav'
    os.system('ffmpeg -i %s -ac 1 %s'%(filename,mono))
    return mono

def pyaudio_featurize(file):
    # use pyaudioanalysis library to export features
    # exported as file[0:-4].json 
    filename=file;
    mono=convert_mono(filename)
    [Fs, x] = audioBasicIO.readAudioFile(mono);
    F = audioFeatureExtraction.stFeatureExtraction(x, Fs, 0.050*Fs, 0.025*Fs);
    os.remove(mono)

    data={
        'features': F[0].tolist()
        }

    jsonfile=open(filename[0:-4]+'.json','w')
    print(jsonfile)
    json.dump(data,jsonfile)
    jsonfile.close() 
    
    # os.system('python pyaudio_help.py %s'%(file))
    jsonfile=file[0:-4]+'.json'
    g=json.load(open(jsonfile))
    features=np.array(g['features'])
    
    # now go through all the features and get statistical features for array
    new_features=list()
    all_labels=['zero crossing rate','energy','entropy of energy','spectral centroid',
                'spectral spread', 'spectral entropy', 'spectral flux', 'spectral rolloff',
                'mfcc1','mfcc2','mfcc3','mfcc4',
                'mfcc5','mfcc6','mfcc7','mfcc8',
                'mfcc9','mfcc10','mfcc11','mfcc12',
                'mfcc13','chroma1','chroma2','chroma3',
                'chroma4','chroma5','chroma6','chroma7',
                'chroma8','chroma9','chroma10','chroma11',
                'chroma12','chroma deviation']
    labels=list()
                
    for i in range(len(features)):
        tfeature=stats(features[i])
        for j in range(len(tfeature)):
            new_features.append(tfeature[j])
            if j==0:
                labels.append('mean '+all_labels[i])
            elif j==1:
                labels.append('std '+all_labels[i])
            elif j==2:
                labels.append('max '+all_labels[i])
            elif j==3:
                labels.append('min '+all_labels[i])
            elif j==4:
                labels.append('median '+all_labels[i])
            
    new_features=np.array(new_features)
    os.remove(jsonfile)
    
    return new_features, labels

In [2]:
predictor_df = pd.read_csv('cv-valid-train.csv')

We will take only the first 15 letters of the filename to get rid of the part of the path that defines the folder the files are in. We need to do this because of the way the loop is defined later.

In [3]:
predictor_df['filename'] = predictor_df['filename'].apply(lambda s: s[15:])

Not every sample is given an age, so we drop these samples. Moreover, we subset the dataframe to only include the filename and the age.

In [4]:
predictor_df = predictor_df[['filename','age']]
predictor_df.dropna(inplace=True)
predictor_df.head()

filename        age
5   sample-000005.mp3   twenties
8   sample-000008.mp3  seventies
13  sample-000013.mp3   thirties
14  sample-000014.mp3    sixties
19  sample-000019.mp3    fifties

We create a loop to featurize each sample and we create a dataframe.

In [5]:
lst = []
extract_labels = pyaudio_featurize('cv-valid-train/sample-000005.mp3')
labels = extract_labels[1]
for sample in list(predictor_df['filename']):
    features = pyaudio_featurize('cv-valid-train/%s'%(sample))
    row = list(features[0])
    row.insert(0,sample)
    lst.append(row)
    
labels.insert(0,'filename')    
df = pd.DataFrame(lst,columns=labels)

<open file 'cv-valid-train/sample-000005.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000005.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000008.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000013.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000014.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000019.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000020.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000023.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000026.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000027.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000029.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000034.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000036.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-0000

<open file 'cv-valid-train/sample-000294.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000297.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000299.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000300.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000303.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000304.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000305.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000317.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000322.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000325.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000333.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000341.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000343.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-0003

<open file 'cv-valid-train/sample-000622.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000625.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000626.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000629.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000633.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000635.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000637.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000639.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000645.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000646.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000647.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000651.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000653.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-0006

<open file 'cv-valid-train/sample-000935.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000936.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000939.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000945.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000947.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000949.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000953.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000957.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000960.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000964.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000967.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000968.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-000972.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-0009

<open file 'cv-valid-train/sample-001237.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001238.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001240.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001245.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001247.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001250.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001255.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001257.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001259.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001260.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001261.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001265.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-001266.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-0012

...

<open file 'cv-valid-train/sample-194485.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194489.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194491.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194492.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194496.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194498.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194504.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194505.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194507.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194510.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194511.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194513.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194519.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-1945

<open file 'cv-valid-train/sample-194779.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194780.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194781.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194782.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194784.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194785.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194787.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194788.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194789.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194790.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194795.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194797.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-194800.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-1948

<open file 'cv-valid-train/sample-195071.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195072.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195084.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195086.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195089.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195091.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195099.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195100.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195102.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195103.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195106.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195107.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195111.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-1951

<open file 'cv-valid-train/sample-195358.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195364.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195366.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195367.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195369.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195372.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195374.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195375.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195376.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195379.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195380.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195381.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-195392.json', mode 'w' at 0x1b163cbc90>
<open file 'cv-valid-train/sample-1953

<open file 'cv-valid-train/sample-195659.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195660.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195667.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195669.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195671.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195673.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195674.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195677.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195682.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195683.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195689.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195690.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-195693.json', mode 'w' at 0x1b163cbed0>
<open file 'cv-valid-train/sample-1956

In [7]:
df

filename  mean zero crossing rate  std zero crossing rate  \
0      sample-000005.mp3                 0.047789                0.042478   
1      sample-000008.mp3                 0.088419                0.072179   
2      sample-000013.mp3                 0.055797                0.034378   
3      sample-000014.mp3                 0.045547                0.048840   
4      sample-000019.mp3                 0.047690                0.054101   
5      sample-000020.mp3                 0.130399                0.098695   
6      sample-000023.mp3                 0.061479                0.041055   
7      sample-000026.mp3                 0.081581                0.068590   
8      sample-000027.mp3                 0.074063                0.067816   
9      sample-000029.mp3                 0.043102                0.058822   
10     sample-000034.mp3                 0.084963                0.058189   
11     sample-000036.mp3                 0.070382                0.060282   
12     sample-000039.mp3                 0.085386                0.097078   
13     sample-000043.mp3                 0.065641                0.053740   
14     sample-000044.mp3                 0.081817                0.056718   
15     sample-000047.mp3                 0.028519                0.042348   
16     sample-000049.mp3                 0.077821                0.061326   
17     sample-000050.mp3                 0.044573                0.050332   
18     sample-000051.mp3                 0.057304                0.074961   
19     sample-000053.mp3                 0.057419                0.047267   
20     sample-000054.mp3                 0.045076                0.045048   
21     sample-000056.mp3                 0.084877                0.062120   
22     sample-000057.mp3                 0.056507                0.043078   
23     sample-000059.mp3                 0.073423                0.066898   
24     sample-000062.mp3                 0.100396                0.066919   
25     sample-000065.mp3                 0.053591                0.048691   
26     sample-000068.mp3                 0.035753                0.032796   
27     sample-000072.mp3                 0.035933                0.023982   
28     sample-000073.mp3                 0.054325                0.062915   
29     sample-000077.mp3                 0.096627                0.080680   
...                  ...                      ...                     ...   
73738  sample-195706.mp3                 0.039113                0.053181   
73739  sample-195707.mp3                 0.061058                0.043865   
73740  sample-195710.mp3                 0.053376                0.058055   
73741  sample-195712.mp3                 0.148859                0.118095   
73742  sample-195720.mp3                 0.047732                0.041728   
73743  sample-195723.mp3                 0.027116                0.041174   
73744  sample-195729.mp3                 0.029974                0.016456   
73745  sample-195731.mp3                 0.066654                0.047994   
73746  sample-195733.mp3                 0.130201                0.119263   
73747  sample-195739.mp3                 0.038367                0.031277   
73748  sample-195741.mp3                 0.098460                0.067460   
73749  sample-195742.mp3                 0.024042                0.031585   
73750  sample-195743.mp3                 0.043761                0.052799   
73751  sample-195746.mp3                 0.037244                0.025447   
73752  sample-195747.mp3                 0.047012                0.053569   
73753  sample-195748.mp3                 0.046245                0.044091   
73754  sample-195749.mp3                 0.046218                0.055191   
73755  sample-195750.mp3                 0.073533                0.054553   
73756  sample-195751.mp3                 0.050605                0.060559   
73757  sample-195756.mp3                 0.047352                0.042806   
73758  sampl

We merge the two dataframes on the column 'filename' so we can create a DataFrame with the audio features, as well as the age category.

In [15]:
new_df = df.merge(predictor_df,on='filename')

In [16]:
new_df

filename  mean zero crossing rate  std zero crossing rate  \
0      sample-000005.mp3                 0.047789                0.042478   
1      sample-000008.mp3                 0.088419                0.072179   
2      sample-000013.mp3                 0.055797                0.034378   
3      sample-000014.mp3                 0.045547                0.048840   
4      sample-000019.mp3                 0.047690                0.054101   
5      sample-000020.mp3                 0.130399                0.098695   
6      sample-000023.mp3                 0.061479                0.041055   
7      sample-000026.mp3                 0.081581                0.068590   
8      sample-000027.mp3                 0.074063                0.067816   
9      sample-000029.mp3                 0.043102                0.058822   
10     sample-000034.mp3                 0.084963                0.058189   
11     sample-000036.mp3                 0.070382                0.060282   
12     sample-000039.mp3                 0.085386                0.097078   
13     sample-000043.mp3                 0.065641                0.053740   
14     sample-000044.mp3                 0.081817                0.056718   
15     sample-000047.mp3                 0.028519                0.042348   
16     sample-000049.mp3                 0.077821                0.061326   
17     sample-000050.mp3                 0.044573                0.050332   
18     sample-000051.mp3                 0.057304                0.074961   
19     sample-000053.mp3                 0.057419                0.047267   
20     sample-000054.mp3                 0.045076                0.045048   
21     sample-000056.mp3                 0.084877                0.062120   
22     sample-000057.mp3                 0.056507                0.043078   
23     sample-000059.mp3                 0.073423                0.066898   
24     sample-000062.mp3                 0.100396                0.066919   
25     sample-000065.mp3                 0.053591                0.048691   
26     sample-000068.mp3                 0.035753                0.032796   
27     sample-000072.mp3                 0.035933                0.023982   
28     sample-000073.mp3                 0.054325                0.062915   
29     sample-000077.mp3                 0.096627                0.080680   
...                  ...                      ...                     ...   
73738  sample-195706.mp3                 0.039113                0.053181   
73739  sample-195707.mp3                 0.061058                0.043865   
73740  sample-195710.mp3                 0.053376                0.058055   
73741  sample-195712.mp3                 0.148859                0.118095   
73742  sample-195720.mp3                 0.047732                0.041728   
73743  sample-195723.mp3                 0.027116                0.041174   
73744  sample-195729.mp3                 0.029974                0.016456   
73745  sample-195731.mp3                 0.066654                0.047994   
73746  sample-195733.mp3                 0.130201                0.119263   
73747  sample-195739.mp3                 0.038367                0.031277   
73748  sample-195741.mp3                 0.098460                0.067460   
73749  sample-195742.mp3                 0.024042                0.031585   
73750  sample-195743.mp3                 0.043761                0.052799   
73751  sample-195746.mp3                 0.037244                0.025447   
73752  sample-195747.mp3                 0.047012                0.053569   
73753  sample-195748.mp3                 0.046245                0.044091   
73754  sample-195749.mp3                 0.046218                0.055191   
73755  sample-195750.mp3                 0.073533                0.054553   
73756  sample-195751.mp3                 0.050605                0.060559   
73757  sample-195756.mp3                 0.047352                0.042806   
73758  sampl

In [17]:
new_df.to_csv('audio_training_data_cleaned.csv') # export cleaned data as csv file